# Assessing GDPR-Compliance in Web Applications: A Machine Learning Approach

We will assess the GDPR-compliance of web applications based on their privacy policies. We use a classification model, trained on a corpus of 18,397 natural sentences, to classify the privacy policies on whether five General Data Protection Regulation (GDPR) privacy policy core requirements are communicated in the policy.

__Relevance:__ The GDPR applies to any personal data processing of EU citizens. We aim to assess the state of GDPR-compliance in application software based on their privacy policies.

__Focus:__ web applications; as the web application paradigm is widely used due to the omnipresence of web browsers across PCs and mobile devices. In particular, we focus on organisations that provide cloud-based solutions: Cloud Computing, Cloud Data Services, Cloud Infrastructure, Cloud, Management, and Cloud Storage.


__Goal:__ to scrutinize the privacy policies of web applications using ML, to assess whether core privacy policy requirements are communicated.

#### __RQ:__ What is the state of GDPR-compliance disclosure in web applications?

---

### Step 1: collect list of companies active in the Web Apps industry

To do so we utilize the Crunchbase database that allows us to identify companies that provide webbased services, filtered on location (which in our case will be the European Union). We used 

We've imported 2792 companies using the following criteria:
- Industry: Web Services -> Cloud Computing, Cloud Data Services, Cloud Infrastructure, Cloud, Management, and Cloud Storage
- Location: USA, India, EU

---

In [39]:
import os
from newspaper import Article
from bs4 import BeautifulSoup
from six.moves.urllib.parse import urlparse
import urllib
import sys
import time
import nltk
import glob
import pandas as pd
import requests
import spacy
import random
# from googlesearch import search
from langdetect import detect
import re
import pickle
import math
import numpy as np
import collections
from nltk.stem import PorterStemmer
from nltk.corpus import stopwords
import re
from tabulate import tabulate
from IPython.display import display, HTML

### Step 2: read data

In [40]:
path = r'C:\Users\aaberkan\OneDrive - UGent\Scripts\GDPR-Compliance in Web Applications\data\Crunchbase\Cloud'
filenames = glob.glob(path + "/*.csv")

In [41]:
# len = 30
len(filenames)

30

In [42]:
dfs = []
for filename in filenames:
    dfs.append(pd.read_csv(filename))

In [43]:
crunch_data = pd.concat(dfs, ignore_index=True)

In [44]:
crunch_data

Organization Name  \
0                 Ex Libris   
1                     Exact   
2                 Xperience   
3                      Sage   
4                    Novahé   
...                     ...   
21235          BackupAddict   
21236  NetConvergence, Inc.   
21237         MyLabBook.com   
21238              Radmedix   
21239    Knockout PC Repair   

                                   Organization Name URL  \
0      https://www.crunchbase.com/organization/ex-libris   
1          https://www.crunchbase.com/organization/exact   
2      https://www.crunchbase.com/organization/xperie...   
3      https://www.crunchbase.com/organization/sage-c1e4   
4         https://www.crunchbase.com/organization/novahé   
...                                                  ...   
21235  https://www.crunchbase.com/organization/backup...   
21236  https://www.crunchbase.com/organization/netcon...   
21237  https://www.crunchbase.com/organization/mylabb...   
21238   https://www.crunchbase.com/organization/radmedix   
21239  https://www.crunchbase.com/organization/knocko...   

                                        Full Description  \
0      Ex Libris Group is a leading provider of libra...   
1      Exact is a global supplier of cloud business s...   
2      Xperience provides software solutions within E...   
3      Sage DPW-Software is now implementing over 100...   
4                                                    NaN   
...                                                  ...   
21235                                                NaN   
21236                                                NaN   
21237                                                NaN   
21238                                                NaN   
21239                                                NaN   

                                              Industries  \
0      Apps, Cloud Computing, Enterprise Software, In...   
1      Accounting, Cloud Computing, CRM, Enterprise R...   
2      Cloud Computing, Consulting, CRM, Enterprise R...   
3      Cloud Computing, Computer, Private Cloud, Secu...   
4      Cloud Computing, Information Technology, IT In...   
...                                                  ...   
21235  Cloud Storage, Information Technology, Profess...   
21236  Cloud Storage, Enterprise Software, Informatio...   
21237       Cloud Data Services, Cloud Storage, Software   
21238  Cloud Storage, Manufacturing, Medical Device, ...   
21239  Cloud Storage, Information Technology, IT Mana...   

                                Website  \
0          http://www.exlibrisgroup.com   
1                  http://www.exact.com   
2      https://www.xperience-group.com/   
3               https://www.sagedpw.at/   
4                https://www.novahe.fr/   
...                                 ...   
21235     https://www.backupaddict.com/   
21236     http://www.netconvergence.com   
21237         https://www.mylabbook.com   
21238              https://radmedix.com   
21239     https://knockoutpcrepair.com/   

                           Headquarters Location  \
0                 Ballerup, Hovedstaden, Denmark   
1           Delft, Zuid-Holland, The Netherlands   
2                 Antrim, Antrim, United Kingdom   
3                          Vienna, Wien, Austria   
4                        Orléans, Centre, France   
...                                          ...   
21235  Jersey Shore, Pennsylvania, United States   
21236     Santa Clara, California, United States   
21237       Texas, South Carolina, United States   
21238                Dayton, Ohio, United States   
21239       Brentwood, California, United States   

                                             Description CB Rank (Company)  \
0      Ex Libris Group is a leading provider of libra...           165,720   
1      Exact is a company that provides cloud based b...           229,780   
2      Xperience provides software solutions within E...           187,002   
3                Sag

In [45]:
crunch_data.loc[crunch_data['Organization Name'] == "Cloud&Heat Technologies"]

Organization Name  \
16661  Cloud&Heat Technologies   

                                 Organization Name URL  \
16661  https://www.crunchbase.com/organization/aoterra   

                                        Full Description  \
16661  Since its foundation in 2011, Cloud&Heat’s mis...   

                                              Industries  \
16661  Cloud Infrastructure, Data Center, Energy, Inf...   

                           Website      Headquarters Location  \
16661  http://www.cloudandheat.com  Dresden, Sachsen, Germany   

                                             Description CB Rank (Company)  \
16661  Cloud&Heat Technologies develops, builds and o...           100,269   

      SEMrush - Monthly Visits SEMrush - Average Visits (6 months)  ...  \
16661                    2,680                           13,489.67  ...   

      Founded Date Founded Date Precision Number of Founders  \
16661   2011-11-01                    day                4.0   

       Number of Employees                                           Founders  \
16661              101-250  Christof Fetzer, Jens Struckmeier, Marcel Schr...   

      Apptopia - Number of Apps Apptopia - Downloads Last 30 Days  \
16661                       NaN                               NaN   

      Aberdeen - IT Spend Aberdeen - IT Spend Currency  \
16661           6566431.0                          USD   

      Aberdeen - IT Spend Currency (in USD)  
16661                             6566431.0  

[1 rows x 32 columns]

In [46]:
# crunch_data = crunch_data[((10267) + 4244):].copy(deep=True)
crunch_data = crunch_data[16662:].copy(deep=True)

In [47]:
# remove duplicates
crunch_data.drop_duplicates(inplace=True)

In [48]:
crunch_data

Organization Name  \
16662       Genese Solution   
16663              Polyaxon   
16664            Mainstream   
16665             ClusterCS   
16666                Replex   
...                     ...   
21235          BackupAddict   
21236  NetConvergence, Inc.   
21237         MyLabBook.com   
21238              Radmedix   
21239    Knockout PC Repair   

                                   Organization Name URL  \
16662  https://www.crunchbase.com/organization/genese...   
16663   https://www.crunchbase.com/organization/polyaxon   
16664  https://www.crunchbase.com/organization/mainst...   
16665  https://www.crunchbase.com/organization/clustercs   
16666  https://www.crunchbase.com/organization/replex...   
...                                                  ...   
21235  https://www.crunchbase.com/organization/backup...   
21236  https://www.crunchbase.com/organization/netcon...   
21237  https://www.crunchbase.com/organization/mylabb...   
21238   https://www.crunchbase.com/organization/radmedix   
21239  https://www.crunchbase.com/organization/knocko...   

                                        Full Description  \
16662  We are an official Cloud Consulting Provider o...   
16663                                                NaN   
16664                                                NaN   
16665  ClusterCS is a Cloud-Based Linux Control Panel...   
16666  Replex is the first governance and cost manage...   
...                                                  ...   
21235                                                NaN   
21236                                                NaN   
21237                                                NaN   
21238                                                NaN   
21239                                                NaN   

                                              Industries  \
16662  Cloud Computing, Cloud Infrastructure, Cloud M...   
16663  Artificial Intelligence, Cloud Infrastructure,...   
16664  Cloud Infrastructure, Information Technology, ...   
16665  Cloud Computing, Cloud Infrastructure, Cloud M...   
16666  Cloud Infrastructure, Cloud Management, Inform...   
...                                                  ...   
21235  Cloud Storage, Information Technology, Profess...   
21236  Cloud Storage, Enterprise Software, Informatio...   
21237       Cloud Data Services, Cloud Storage, Software   
21238  Cloud Storage, Manufacturing, Medical Device, ...   
21239  Cloud Storage, Information Technology, IT Mana...   

                               Website  \
16662  https://www.genesesolution.com/   
16663             https://polyaxon.com   
16664        https://www.mainstream.rs   
16665       https://www.clustercs.com/   
16666            https://www.replex.io   
...                                ...   
21235    https://www.backupaddict.com/   
21236    http://www.netconvergence.com   
21237        https://www.mylabbook.com   
21238             https://radmedix.com   
21239    https://knockoutpcrepair.com/   

                           Headquarters Location  \
16662            London, England, United Kingdom   
16663                    Berlin, Berlin, Germany   
16664                Belgrade, Vojvodina, Serbia   
16665              Bucharest, Bucuresti, Romania   
16666                  Leipzig, Sachsen, Germany   
...                                          ...   
21235  Jersey Shore, Pennsylvania, United States   
21236     Santa Clara, California, United States   
21237       Texas, South Carolina, United States   
21238                Dayton, Ohio, United States   
21239       Brentwood, California, United States   

                                             Description CB Rank (Company)  \
16662  As an official Cloud Consulting Provider of Am...           439,251   
16663  An open source platform for reproducible machi...           208,230   
16664  Mainstream provides advanced cloud, managed ho...           439,301   
16665  ClusterCS is a Cloud-Base

In [49]:
crunch_data.to_csv("crunch_cloud_conc_p3.csv", sep='\t', header=True, index=False)

#### Clean websites list

In [50]:
websites_list = crunch_data["Website"].tolist()

In [51]:
len(websites_list)

4259

In [52]:
# remove / from the end of the string that contains the website
# websites_list = [website.rstrip(website[-1]) if (website[-1] == "/") else website for website in websites_list]
websites_list = [website.rstrip(website[-1]) if (isinstance(website, str) and website[-1] == "/") else website for website in websites_list]
# een keer extra voor het geval er een url was met // op het eind
websites_list = [website.rstrip(website[-1]) if (isinstance(website, str) and website[-1] == "/") else website for website in websites_list]

In [53]:
len(websites_list)

4259

---

### Step 3: scrape privacy policies

In [54]:
def get_privacy_policy_url(query):
    keyword_in_title = 0
    attempts = 0
    url = ""
    print("Query: " + query)
    
    try:
        query_results_list = return_google_results(query, 3, 5)
        print("Considering " + str(len(query_results_list)) + " URL(s) ...")
        for i, url in enumerate(query_results_list):
            term_in_url = 0
            attempts = attempts + 1
            print("Assessing privacy policy URL: " + url)
            
            if (re.findall('privacy', url) or re.findall('policy', url) or re.findall('gdpr', url) 
                or re.findall('terms', url) or re.findall('legal', url)): 
                print("Found relevant terms in URL! Succesful break!")
                break

#                     pass
            if keyword_in_title == 1 or attempts == 3 or i==(len(query_results_list)-1): 
                keyword_in_title = 0
                attempts = 0
                print("No results. Breaking ..")
                url = ""
#                 print(sentences)
                break   
    except Exception as e:
            print(str(e))
            pass
    return url

In [55]:
def return_google_results(keywords, num_results, attempts):
    user_agent_list = [
      'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_5) AppleWebKit/605.1.15 (KHTML, like Gecko) Version/13.1.1 Safari/605.1.15',
      'Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:77.0) Gecko/20100101 Firefox/77.0',
      'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_5) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/83.0.4103.97 Safari/537.36',
      'Mozilla/5.0 (Macintosh; Intel Mac OS X 10.15; rv:77.0) Gecko/20100101 Firefox/77.0',
      'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/83.0.4103.97 Safari/537.36',
    ]

    html_keywords = urllib.parse.quote_plus(keywords)
    sleep_init = 10
    
    url = "https://www.google.com/search?q=" + html_keywords + "&num=" + str(num_results)
    print("** Search query in URL: " + url)

    headers = {'User-Agent': random.choice(user_agent_list)}
    
    html = requests.get(url, headers=headers)

    if html.status_code == 429:
        if(attempts == 0):
            sys.exit("Too many request 429, attempted "+ str(5)+ " times, break ...")
        else:
            if 'Retry_After' in html.headers:
                print("Helaas, geen retry-after info")
            else:
                time.sleep(sleep_init)
                print("Too many requests (attempt "+ str(5 - attempts)+ "), we will attempt again in " + str(sleep_init) + " seconds")
                return_google_results(keywords, num_results, (attempts - 1))
    else: 
        pass
        
    soup = BeautifulSoup(html.text, 'html.parser')

    allData = soup.find_all("div",{"class":"g"})

    link_list = []
    print("len alldata: " + str(len(allData)))
    
    for i in range(0,len(allData)):
        link = allData[i].find('a').get('href')
        
        if(link is not None):
            if(link.find('https') != -1 and link.find('http') == 0 and link.find('aclk') == -1):
                print(link)
                link_list.append(link)
    print(link_list)
    return link_list

#### Collect privacy policy URLs

In [72]:
privacy_policies_url_list = []

In [73]:
# loop through each company URL and attempt to find the URL of the privacy policy
count_urls = 0
for i, url_company in enumerate(websites_list):    
    print(i)

#     print(len(privacy_policies_url_list))
    if(isinstance("url_company", str) is False or (url_company == url_company) is False):
        privacy_policies_url_list.append("")
    else:
        query = "site:\"" + url_company + " \"privacy policy"
        privacy_policies_url_list.append(get_privacy_policy_url(query))
        if(len(privacy_policies_url_list[-1]) > 0):
            count_urls = count_urls + 1
    print("URL count: " + str(count_urls))
    print()
    time.sleep(50)

0
Query: site:"https://www.genesesolution.com "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22https%3A%2F%2Fwww.genesesolution.com+%22privacy+policy&num=3
len alldata: 2
https://www.genesesolution.com/bd/privacy-policy/
https://www.genesesolution.com/cookie-policy/
['https://www.genesesolution.com/bd/privacy-policy/', 'https://www.genesesolution.com/cookie-policy/']
Considering 2 URL(s) ...
Assessing privacy policy URL: https://www.genesesolution.com/bd/privacy-policy/
Found relevant terms in URL! Succesful break!
URL count: 1

1
Query: site:"https://polyaxon.com "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22https%3A%2F%2Fpolyaxon.com+%22privacy+policy&num=3
len alldata: 2
https://polyaxon.com/privacy/
https://polyaxon.com/terms/
['https://polyaxon.com/privacy/', 'https://polyaxon.com/terms/']
Considering 2 URL(s) ...
Assessing privacy policy URL: https://polyaxon.com/privacy/
Found relevant terms in URL! Succesful b

17
Query: site:"http://www.bimplus.net "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22http%3A%2F%2Fwww.bimplus.net+%22privacy+policy&num=3
len alldata: 1
https://www.bimplus.net/data-protection
['https://www.bimplus.net/data-protection']
Considering 1 URL(s) ...
Assessing privacy policy URL: https://www.bimplus.net/data-protection
No results. Breaking ..
URL count: 8

18
Query: site:"https://playboxneo.com "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22https%3A%2F%2Fplayboxneo.com+%22privacy+policy&num=3
len alldata: 2
https://playboxneo.com/privacy-policy
https://playboxneo.com/quick-contact
['https://playboxneo.com/privacy-policy', 'https://playboxneo.com/quick-contact']
Considering 2 URL(s) ...
Assessing privacy policy URL: https://playboxneo.com/privacy-policy
Found relevant terms in URL! Succesful break!
URL count: 9

19
Query: site:"https://www.coursepath.com "privacy policy
** Search query in URL: https://www.

len alldata: 2
https://www.cloudsolutions4biz.com/privacy-policy
https://www.cloudsolutions4biz.com/gdpr---general-data-protection-policy
['https://www.cloudsolutions4biz.com/privacy-policy', 'https://www.cloudsolutions4biz.com/gdpr---general-data-protection-policy']
Considering 2 URL(s) ...
Assessing privacy policy URL: https://www.cloudsolutions4biz.com/privacy-policy
Found relevant terms in URL! Succesful break!
URL count: 19

36
Query: site:"http://www.velobility.net "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22http%3A%2F%2Fwww.velobility.net+%22privacy+policy&num=3
len alldata: 0
[]
Considering 0 URL(s) ...
URL count: 19

37
Query: site:"https://www.anynines.com "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22https%3A%2F%2Fwww.anynines.com+%22privacy+policy&num=3
len alldata: 2
https://www.anynines.com/data-privacy
https://www.anynines.com/contact
['https://www.anynines.com/data-privacy', 'https://www.anynines.

len alldata: 2
https://www.simplecloud.io/en/privacy-policy.html
https://www.simplecloud.io/en/privacy-cookies.html
['https://www.simplecloud.io/en/privacy-policy.html', 'https://www.simplecloud.io/en/privacy-cookies.html']
Considering 2 URL(s) ...
Assessing privacy policy URL: https://www.simplecloud.io/en/privacy-policy.html
Found relevant terms in URL! Succesful break!
URL count: 28

54
Query: site:"https://itsvit.com "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22https%3A%2F%2Fitsvit.com+%22privacy+policy&num=3
len alldata: 2
https://itsvit.com/privacy-policy/
https://itsvit.com/cookie-policy/
['https://itsvit.com/privacy-policy/', 'https://itsvit.com/cookie-policy/']
Considering 2 URL(s) ...
Assessing privacy policy URL: https://itsvit.com/privacy-policy/
Found relevant terms in URL! Succesful break!
URL count: 29

55
Query: site:"https://www.projetia.fr "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22https%3A%2F

73
Query: site:"https://busywork.co "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22https%3A%2F%2Fbusywork.co+%22privacy+policy&num=3
len alldata: 0
[]
Considering 0 URL(s) ...
URL count: 35

74
Query: site:"https://stuart.be "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22https%3A%2F%2Fstuart.be+%22privacy+policy&num=3
len alldata: 2
https://stuart.be/en/privacy/
https://stuart.be/en/insight/gdpr-explained-in-plain-language/
['https://stuart.be/en/privacy/', 'https://stuart.be/en/insight/gdpr-explained-in-plain-language/']
Considering 2 URL(s) ...
Assessing privacy policy URL: https://stuart.be/en/privacy/
Found relevant terms in URL! Succesful break!
URL count: 36

75
Query: site:"https://www.saqqarainformatica.com "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22https%3A%2F%2Fwww.saqqarainformatica.com+%22privacy+policy&num=3
len alldata: 0
[]
Considering 0 URL(s) ...
URL count: 36



...

len alldata: 0
[]
Considering 0 URL(s) ...
URL count: 1619

4146
Query: site:"http://www.onsitenc.com "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22http%3A%2F%2Fwww.onsitenc.com+%22privacy+policy&num=3
len alldata: 0
[]
Considering 0 URL(s) ...
URL count: 1619

4147
Query: site:"http://ansnetworking.com "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22http%3A%2F%2Fansnetworking.com+%22privacy+policy&num=3
len alldata: 1
https://www.ansnetworking.com/privacy-policy/
['https://www.ansnetworking.com/privacy-policy/']
Considering 1 URL(s) ...
Assessing privacy policy URL: https://www.ansnetworking.com/privacy-policy/
Found relevant terms in URL! Succesful break!
URL count: 1620

4148
Query: site:"https://www.portolasystems.net "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22https%3A%2F%2Fwww.portolasystems.net+%22privacy+policy&num=3
len alldata: 0
[]
Considering 0 URL(s) ...
URL count: 1

len alldata: 1
[]
Considering 0 URL(s) ...
URL count: 1629

4168
Query: site:"https://drive.tabania.com "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22https%3A%2F%2Fdrive.tabania.com+%22privacy+policy&num=3
len alldata: 2
https://drive.tabania.com/page/privacy-policy
https://drive.tabania.com/page/terms-of-service
['https://drive.tabania.com/page/privacy-policy', 'https://drive.tabania.com/page/terms-of-service']
Considering 2 URL(s) ...
Assessing privacy policy URL: https://drive.tabania.com/page/privacy-policy
Found relevant terms in URL! Succesful break!
URL count: 1630

4169
Query: site:"https://www.cloudkoalatech.com "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22https%3A%2F%2Fwww.cloudkoalatech.com+%22privacy+policy&num=3
len alldata: 0
[]
Considering 0 URL(s) ...
URL count: 1630

4170
Query: site:"https://premium-digital.com "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22http

4193
Query: site:"https://dataalign.com "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22https%3A%2F%2Fdataalign.com+%22privacy+policy&num=3
len alldata: 1
https://dataalign.com/
['https://dataalign.com/']
Considering 1 URL(s) ...
Assessing privacy policy URL: https://dataalign.com/
No results. Breaking ..
URL count: 1633

4194
Query: site:"https://www.rainbowsecure.com/geoaclaccesscontrolgateway "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22https%3A%2F%2Fwww.rainbowsecure.com%2Fgeoaclaccesscontrolgateway+%22privacy+policy&num=3
len alldata: 1
https://www.rainbowsecure.com/geoaclaccesscontrolgateway/
['https://www.rainbowsecure.com/geoaclaccesscontrolgateway/']
Considering 1 URL(s) ...
Assessing privacy policy URL: https://www.rainbowsecure.com/geoaclaccesscontrolgateway/
No results. Breaking ..
URL count: 1633

4195
Query: site:"https://docugreen.com "privacy policy
** Search query in URL: https://www.google.com/sear

4215
Query: site:"http://www.triaxis.com "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22http%3A%2F%2Fwww.triaxis.com+%22privacy+policy&num=3
len alldata: 0
[]
Considering 0 URL(s) ...
URL count: 1637

4216
Query: site:"http://www.globaldcim.net "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22http%3A%2F%2Fwww.globaldcim.net+%22privacy+policy&num=3
len alldata: 0
[]
Considering 0 URL(s) ...
URL count: 1637

4217
Query: site:"https://www.viaas.com "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22https%3A%2F%2Fwww.viaas.com+%22privacy+policy&num=3
len alldata: 0
[]
Considering 0 URL(s) ...
URL count: 1637

4218
Query: site:"https://foldercrate.com "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22https%3A%2F%2Ffoldercrate.com+%22privacy+policy&num=3
len alldata: 0
[]
Considering 0 URL(s) ...
URL count: 1637

4219
Query: site:"https://crossroadit.com "privacy

len alldata: 0
[]
Considering 0 URL(s) ...
URL count: 1643

4238
Query: site:"https://rvba.online "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22https%3A%2F%2Frvba.online+%22privacy+policy&num=3
len alldata: 3
https://rvba.online/privacy-policy/
https://rvba.online/about/leadership/
https://rvba.online/wp-content/uploads/2016/11/FINALBroadbandAgendaSept192014RegularMtg-2.pdf
['https://rvba.online/privacy-policy/', 'https://rvba.online/about/leadership/', 'https://rvba.online/wp-content/uploads/2016/11/FINALBroadbandAgendaSept192014RegularMtg-2.pdf']
Considering 3 URL(s) ...
Assessing privacy policy URL: https://rvba.online/privacy-policy/
Found relevant terms in URL! Succesful break!
URL count: 1644

4239
Query: site:"https://www.datasecuritycorp.com "privacy policy
** Search query in URL: https://www.google.com/search?q=site%3A%22https%3A%2F%2Fwww.datasecuritycorp.com+%22privacy+policy&num=3
len alldata: 3
https://www.datasecuritycorp.com/privacy.php

In [74]:
len(privacy_policies_url_list)

4259

In [75]:
(len([(collected_url) for collected_url in privacy_policies_url_list if collected_url is not ""]))

<>:1: SyntaxWarning: "is not" with a literal. Did you mean "!="?
<>:1: SyntaxWarning: "is not" with a literal. Did you mean "!="?
<ipython-input-75-be691173171a>:1: SyntaxWarning: "is not" with a literal. Did you mean "!="?
  (len([(collected_url) for collected_url in privacy_policies_url_list if collected_url is not ""]))


1648

In [77]:
crunch_data['PP URL'] = privacy_policies_url_list

In [78]:
#save data
crunch_data.to_csv("crunch_data_cloud_surv_p3.csv", sep='\t', header=True, index=False)

In [79]:
crunch_data_r = pd.read_csv("crunch_data_cloud_surv_p3.csv", sep='\t', encoding='utf-8')

In [80]:
crunch_data_r

Organization Name                              Organization Name URL  \
0          Genese Solution  https://www.crunchbase.com/organization/genese...   
1                 Polyaxon   https://www.crunchbase.com/organization/polyaxon   
2               Mainstream  https://www.crunchbase.com/organization/mainst...   
3                ClusterCS  https://www.crunchbase.com/organization/clustercs   
4                   Replex  https://www.crunchbase.com/organization/replex...   
...                    ...                                                ...   
4254          BackupAddict  https://www.crunchbase.com/organization/backup...   
4255  NetConvergence, Inc.  https://www.crunchbase.com/organization/netcon...   
4256         MyLabBook.com  https://www.crunchbase.com/organization/mylabb...   
4257              Radmedix   https://www.crunchbase.com/organization/radmedix   
4258    Knockout PC Repair  https://www.crunchbase.com/organization/knocko...   

                                       Full Description  \
0     We are an official Cloud Consulting Provider o...   
1                                                   NaN   
2                                                   NaN   
3     ClusterCS is a Cloud-Based Linux Control Panel...   
4     Replex is the first governance and cost manage...   
...                                                 ...   
4254                                                NaN   
4255                                                NaN   
4256                                                NaN   
4257                                                NaN   
4258                                                NaN   

                                             Industries  \
0     Cloud Computing, Cloud Infrastructure, Cloud M...   
1     Artificial Intelligence, Cloud Infrastructure,...   
2     Cloud Infrastructure, Information Technology, ...   
3     Cloud Computing, Cloud Infrastructure, Cloud M...   
4     Cloud Infrastructure, Cloud Management, Inform...   
...                                                 ...   
4254  Cloud Storage, Information Technology, Profess...   
4255  Cloud Storage, Enterprise Software, Informatio...   
4256       Cloud Data Services, Cloud Storage, Software   
4257  Cloud Storage, Manufacturing, Medical Device, ...   
4258  Cloud Storage, Information Technology, IT Mana...   

                              Website  \
0     https://www.genesesolution.com/   
1                https://polyaxon.com   
2           https://www.mainstream.rs   
3          https://www.clustercs.com/   
4               https://www.replex.io   
...                               ...   
4254    https://www.backupaddict.com/   
4255    http://www.netconvergence.com   
4256        https://www.mylabbook.com   
4257             https://radmedix.com   
4258    https://knockoutpcrepair.com/   

                          Headquarters Location  \
0               London, England, United Kingdom   
1                       Berlin, Berlin, Germany   
2                   Belgrade, Vojvodina, Serbia   
3                 Bucharest, Bucuresti, Romania   
4                     Leipzig, Sachsen, Germany   
...                                         ...   
4254  Jersey Shore, Pennsylvania, United States   
4255     Santa Clara, California, United States   
4256       Texas, South Carolina, United States   
4257                Dayton, Ohio, United States   
4258       Brentwood, California, United States   

                                            Description CB Rank (Company)  \
0     As an official Cloud Consulting Provider of Am...           439,251   
1     An open source platform for reproducible machi...           208,230   
2     Mainstream provides advanced cloud, managed ho...           439,301   
3     ClusterCS is a Cloud-Based Linux Control Panel...           408,356   
4                   Replex provides software solutions.            26,882   
...                                               

# Step 3: Scrape privacy policies

In [81]:
nlp = spacy.load("en_core_web_md")

In [82]:
def scrape_policies_google(url):
    policies = []
    sentences = []    
    try:
        
        article = Article(url)
#             print(url)
        article.download() #Downloads the link’s HTML content
#             print(url)
        article.parse() #Parse the article
#             print(url)
#                 print(article.title)
        doc = nlp(article.text)
        print("PP language = EN?: " + str(detect(article.text) == 'en'))
        print("PP length > 10 sentences?: " + str(len(list(doc.sents)) > 10))

        if detect(article.text) == 'en' and len(list(doc.sents)) > 10:
            print("Policy meets requirements of language and length ... ")
            sentences = list(doc.sents)
            print("Scraping successful!")

        else:
            print("Scraping not successful")
    except:
            pass
    print()
    return sentences

In [83]:
pp_list_sentences = []
for i, pp_url in enumerate(privacy_policies_url_list):
    print(i)
    if pp_url == "":
        pp_list_sentences.append("")
    else:
        pp_list_sentences.append(scrape_policies_google(pp_url))

0
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

1
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

2
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3
4
5
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

6
7
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

8
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

9
10
11
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

12
13
14

15
16
17
18
PP language = EN?: True
PP l

Scraping successful!

159
160
161
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

162
163
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

164
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

165
166
167
168
169
170
171
172
173
174
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

175
176
177
178
179
180
181
182
183
184
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

185
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

186
187
188
189
190
191
192
193
194
195
196
PP language = EN?: False
PP length


276
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

277
278
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

279
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

280
281

282
283
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

284
285
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

286
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

287
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

288
289
290
291
292
293
29


397
PP language = EN?: False
PP length > 10 sentences?: True
Scraping not successful

398
399
400
401
402
403
404
405
PP language = EN?: False
PP length > 10 sentences?: True
Scraping not successful

406
407
408
409
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

410
411
412
413
414
PP language = EN?: False
PP length > 10 sentences?: True
Scraping not successful

415
416
417
418
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

419
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

420
421
422
423
424
425
426
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

427

428
429
PP language = EN?: True
PP length > 10 sentences?: False
Scraping not successful

430
431
43


625
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

626
627
628
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

629
630
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

631
632
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

633
634
PP language = EN?: True
PP length > 10 sentences?: False
Scraping not successful

635
636
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

637
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

638
639
PP language = EN?: True
PP length > 10 sentences?: False
Scraping

...

PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3500
3501
3502
3503
3504
3505
3506
3507
3508
3509
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3510
3511
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3512
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3513
3514
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3515
3516
3517
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3518
3519
3520
3521
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and 

PP language = EN?: True
PP length > 10 sentences?: False
Scraping not successful

3695
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3696
3697
3698
PP language = EN?: True
PP length > 10 sentences?: False
Scraping not successful

3699
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3700
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3701
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3702
3703
PP language = EN?: True
PP length > 10 sentences?: False
Scraping not successful

3704
3705
3706
3707
3708
3709
3710
3711

3712
3713
3714
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping succes

PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3945
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3946
3947
3948

3949
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3950
3951
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3952
3953
3954
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3955
3956
3957

3958
3959
3960

3961
3962
3963
3964
3965
PP language = EN?: False
PP length > 10 sentences?: True
Scraping not successful

3966
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3967
3968
PP 


3973
3974
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3975
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3976
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3977
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3978
3979
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3980
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3981
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

3982
3983
3984
PP language = E

PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

4097
4098
4099
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

4100
4101
4102
4103
4104
4105
4106
4107
4108

4109
4110
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

4111
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

4112
4113

4114
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

4115
PP language = EN?: True
PP length > 10 sentences?: True
Policy meets requirements of language and length ... 
Scraping successful!

4116
PP language = EN?: True
PP length > 10 sentences?: False
Scraping not successful

4117
PP language = EN?: 

In [84]:
[print(len(pp)) for pp in pp_list_sentences]

118
79
38
0
0
280
0
65
41
0
0
188
0
0
0
0
0
0
58
177
11
0
0
0
0
0
0
45
50
56
20
0
0
94
37
51
0
385
0
0
0
0
107
150
0
0
0
0
12
181
0
354
0
37
71
0
30
129
0
113
0
0
0
0
0
0
0
0
0
0
170
125
0
0
60
0
0
100
0
0
0
0
98
0
0
60
12
0
0
0
0
0
0
0
0
221
286
0
30
0
89
0
0
0
0
0
0
0
59
0
0
69
0
45
0
0
87
0
0
134
0
0
92
0
0
0
0
0
0
111
0
0
0
0
59
0
0
50
138
0
60
0
0
23
59
0
0
0
0
0
0
107
0
129
0
0
0
0
91
0
0
203
0
11
122
0
0
0
0
0
0
0
0
0
116
0
0
0
0
0
0
0
0
0
229
84
0
0
0
0
0
0
0
0
0
0
0
0
258
0
0
0
0
0
141
0
72
0
0
56
73
139
0
0
0
0
0
66
114
0
0
161
0
0
0
0
0
0
0
61
88
0
0
0
0
0
0
0
0
0
0
0
0
101
47
0
0
49
0
11
0
0
0
22
0
73
0
0
0
0
55
0
62
0
0
0
0
0
0
0
0
0
0
0
0
0
88
0
473
194
0
0
0
43
0
183
226
12
0
0
0
0
0
0
0
191
0
0
0
0
0
134
0
0
0
0
0
0
0
0
0
58
0
75
0
84
0
0
77
0
0
0
124
0
105
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
111
0
181
0
0
0
42
0
0
0
0
0
0
0
0
0
270
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
53
0
0
0
0
0
66
0
0
0
0
0
0
0
0
0
0
0
155
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
80
0
0
0
0
0
0
0
0
30
105
0
0
0
0
0
0

0
17
0
154
0
0
0
52
0
0
65
0
0
0
13
0
0
0
78
0
0
0
0
98
0
0
0
0
194
0
0
0
358
94
41
0
20
29
133
0
0
0
0
0
53
0
0
0
0
0
0
0
0
0
0
49
0
0
0
0
0
0
0
0
0
0
113
0
0
0
0
0
0
0
0
0
0
14
0
0
0
0
0
0
186
0
0
0
51
0
0
0
0
0
0
0
0
0
0
16
17
0
0
0
0
0
0
0
0
0
66
0
204
30
0
0
0
191
0
0
0
0
0
0
0
0
0
0
86
0
0
143
0


[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,

# Step 4: Classification

In [85]:
crunch_data_r

Organization Name                              Organization Name URL  \
0          Genese Solution  https://www.crunchbase.com/organization/genese...   
1                 Polyaxon   https://www.crunchbase.com/organization/polyaxon   
2               Mainstream  https://www.crunchbase.com/organization/mainst...   
3                ClusterCS  https://www.crunchbase.com/organization/clustercs   
4                   Replex  https://www.crunchbase.com/organization/replex...   
...                    ...                                                ...   
4254          BackupAddict  https://www.crunchbase.com/organization/backup...   
4255  NetConvergence, Inc.  https://www.crunchbase.com/organization/netcon...   
4256         MyLabBook.com  https://www.crunchbase.com/organization/mylabb...   
4257              Radmedix   https://www.crunchbase.com/organization/radmedix   
4258    Knockout PC Repair  https://www.crunchbase.com/organization/knocko...   

                                       Full Description  \
0     We are an official Cloud Consulting Provider o...   
1                                                   NaN   
2                                                   NaN   
3     ClusterCS is a Cloud-Based Linux Control Panel...   
4     Replex is the first governance and cost manage...   
...                                                 ...   
4254                                                NaN   
4255                                                NaN   
4256                                                NaN   
4257                                                NaN   
4258                                                NaN   

                                             Industries  \
0     Cloud Computing, Cloud Infrastructure, Cloud M...   
1     Artificial Intelligence, Cloud Infrastructure,...   
2     Cloud Infrastructure, Information Technology, ...   
3     Cloud Computing, Cloud Infrastructure, Cloud M...   
4     Cloud Infrastructure, Cloud Management, Inform...   
...                                                 ...   
4254  Cloud Storage, Information Technology, Profess...   
4255  Cloud Storage, Enterprise Software, Informatio...   
4256       Cloud Data Services, Cloud Storage, Software   
4257  Cloud Storage, Manufacturing, Medical Device, ...   
4258  Cloud Storage, Information Technology, IT Mana...   

                              Website  \
0     https://www.genesesolution.com/   
1                https://polyaxon.com   
2           https://www.mainstream.rs   
3          https://www.clustercs.com/   
4               https://www.replex.io   
...                               ...   
4254    https://www.backupaddict.com/   
4255    http://www.netconvergence.com   
4256        https://www.mylabbook.com   
4257             https://radmedix.com   
4258    https://knockoutpcrepair.com/   

                          Headquarters Location  \
0               London, England, United Kingdom   
1                       Berlin, Berlin, Germany   
2                   Belgrade, Vojvodina, Serbia   
3                 Bucharest, Bucuresti, Romania   
4                     Leipzig, Sachsen, Germany   
...                                         ...   
4254  Jersey Shore, Pennsylvania, United States   
4255     Santa Clara, California, United States   
4256       Texas, South Carolina, United States   
4257                Dayton, Ohio, United States   
4258       Brentwood, California, United States   

                                            Description CB Rank (Company)  \
0     As an official Cloud Consulting Provider of Am...           439,251   
1     An open source platform for reproducible machi...           208,230   
2     Mainstream provides advanced cloud, managed ho...           439,301   
3     ClusterCS is a Cloud-Based Linux Control Panel...           408,356   
4                   Replex provides software solutions.            26,882   
...                                               

In [86]:
GDPR_classes = ['DPO', 'Purpose', 'Acquired data', 'Data sharing', 'Rights']

In [87]:
thresholds = [0.014130434782608696, 0.035326086956521736, 0.017934782608695653, 0.03369565217391304, 0.009782608695652175]

#### Preprocessing

In [88]:
def preprocessing(pps):
#     tokenizer = nlp.tokenizer
    # tokenize sentences
    tokenized_sent = [sent.text.split() for sent in pps]
    
    # remove punctuation
    tokenized_sent = [[re.sub('[,’\'\.!?&“”():*_;"]', '', y) for y in x] for x in tokenized_sent]
    
    # remove words with numbers in them
    tokenized_sent = [[y for y in x if not any(c.isdigit() for c in y)] for x in tokenized_sent]
    
    # remove stopwords   
    tokenized_sent_clean = tokenized_sent
#     tokenized_sent_clean = [[y for y in x if y not in stopwords.words('english')] for x in tokenized_sent]
    
    # from nltk.stem import PorterStemmer
    porter = PorterStemmer()
    tokenized_sent_clean = [[porter.stem(y) for y in x] for x in tokenized_sent_clean]
    
#     lemmatizer = WordNetLemmatizer()
#     tokenized_sent_clean = [[lemmatizer.lemmatize(y) for y in x] for x in tokenized_sent_clean]

    
    detokenized_pps = []
    for i in range(len(tokenized_sent_clean)):
        t = ' '.join(tokenized_sent_clean[i])
        detokenized_pps.append(t) 
    
    return detokenized_pps

In [89]:
def set_GDPR_columns(df):
    df['DPO'] = 0
    df['Purpose'] = 0
    df['Acquired data'] = 0
    df['Data sharing']  = 0
    df['Rights'] = 0

In [90]:
set_GDPR_columns(crunch_data_r)

In [91]:
pp_list_sentences_prep = []

for j, pp in enumerate(pp_list_sentences):
    pp_list_sentences_prep.append(preprocessing(pp))

In [92]:
pp_list_sentences_prep

[['thi privaci polici appli between you the user of thi websit and genes solut limit the owner and provid of thi websit',
  'genes solut limit take the privaci of your inform veri serious',
  'thi privaci polici appli to our use of ani and all data collect by us or provid by you in relat to your use of the websit',
  'definit and interpret',
  'In thi privaci polici the follow definit are use',
  'data collect all inform that you submit to genes solut limit via the websit',
  'thi definit incorpor where applic the definit provid in the data protect law cooki a small text file place on your comput by thi websit when you visit certain part of the websit and/or when you use certain featur of the websit',
  'detail of the cooki use by thi websit are set out in the claus below  cooki  data protect law ani applic law relat to the process of person data includ but not limit to the direct data protect direct or the gdpr and ani nation implement law regul and secondari legisl for as long as the

In [93]:
crunch_data_r['PP text'] = pp_list_sentences_prep

In [94]:
crunch_data_r

Organization Name                              Organization Name URL  \
0          Genese Solution  https://www.crunchbase.com/organization/genese...   
1                 Polyaxon   https://www.crunchbase.com/organization/polyaxon   
2               Mainstream  https://www.crunchbase.com/organization/mainst...   
3                ClusterCS  https://www.crunchbase.com/organization/clustercs   
4                   Replex  https://www.crunchbase.com/organization/replex...   
...                    ...                                                ...   
4254          BackupAddict  https://www.crunchbase.com/organization/backup...   
4255  NetConvergence, Inc.  https://www.crunchbase.com/organization/netcon...   
4256         MyLabBook.com  https://www.crunchbase.com/organization/mylabb...   
4257              Radmedix   https://www.crunchbase.com/organization/radmedix   
4258    Knockout PC Repair  https://www.crunchbase.com/organization/knocko...   

                                       Full Description  \
0     We are an official Cloud Consulting Provider o...   
1                                                   NaN   
2                                                   NaN   
3     ClusterCS is a Cloud-Based Linux Control Panel...   
4     Replex is the first governance and cost manage...   
...                                                 ...   
4254                                                NaN   
4255                                                NaN   
4256                                                NaN   
4257                                                NaN   
4258                                                NaN   

                                             Industries  \
0     Cloud Computing, Cloud Infrastructure, Cloud M...   
1     Artificial Intelligence, Cloud Infrastructure,...   
2     Cloud Infrastructure, Information Technology, ...   
3     Cloud Computing, Cloud Infrastructure, Cloud M...   
4     Cloud Infrastructure, Cloud Management, Inform...   
...                                                 ...   
4254  Cloud Storage, Information Technology, Profess...   
4255  Cloud Storage, Enterprise Software, Informatio...   
4256       Cloud Data Services, Cloud Storage, Software   
4257  Cloud Storage, Manufacturing, Medical Device, ...   
4258  Cloud Storage, Information Technology, IT Mana...   

                              Website  \
0     https://www.genesesolution.com/   
1                https://polyaxon.com   
2           https://www.mainstream.rs   
3          https://www.clustercs.com/   
4               https://www.replex.io   
...                               ...   
4254    https://www.backupaddict.com/   
4255    http://www.netconvergence.com   
4256        https://www.mylabbook.com   
4257             https://radmedix.com   
4258    https://knockoutpcrepair.com/   

                          Headquarters Location  \
0               London, England, United Kingdom   
1                       Berlin, Berlin, Germany   
2                   Belgrade, Vojvodina, Serbia   
3                 Bucharest, Bucuresti, Romania   
4                     Leipzig, Sachsen, Germany   
...                                         ...   
4254  Jersey Shore, Pennsylvania, United States   
4255     Santa Clara, California, United States   
4256       Texas, South Carolina, United States   
4257                Dayton, Ohio, United States   
4258       Brentwood, California, United States   

                                            Description CB Rank (Company)  \
0     As an official Cloud Consulting Provider of Am...           439,251   
1     An open source platform for reproducible machi...           208,230   
2     Mainstream provides advanced cloud, managed ho...           439,301   
3     ClusterCS is a Cloud-Based Linux Control Panel...           408,356   
4                   Replex provides software solutions.            26,882   
...                                               

In [95]:
crunch_data_r.to_csv("crunch_data_pp_url_text_p3.csv", sep='\t', header=True)

#### Classification

In [96]:
crunch_data_r = pd.read_csv("crunch_data_pp_url_text_p3.csv", sep='\t', encoding='utf-8', index_col = 0)

In [97]:
crunch_data_r

Organization Name                              Organization Name URL  \
0          Genese Solution  https://www.crunchbase.com/organization/genese...   
1                 Polyaxon   https://www.crunchbase.com/organization/polyaxon   
2               Mainstream  https://www.crunchbase.com/organization/mainst...   
3                ClusterCS  https://www.crunchbase.com/organization/clustercs   
4                   Replex  https://www.crunchbase.com/organization/replex...   
...                    ...                                                ...   
4254          BackupAddict  https://www.crunchbase.com/organization/backup...   
4255  NetConvergence, Inc.  https://www.crunchbase.com/organization/netcon...   
4256         MyLabBook.com  https://www.crunchbase.com/organization/mylabb...   
4257              Radmedix   https://www.crunchbase.com/organization/radmedix   
4258    Knockout PC Repair  https://www.crunchbase.com/organization/knocko...   

                                       Full Description  \
0     We are an official Cloud Consulting Provider o...   
1                                                   NaN   
2                                                   NaN   
3     ClusterCS is a Cloud-Based Linux Control Panel...   
4     Replex is the first governance and cost manage...   
...                                                 ...   
4254                                                NaN   
4255                                                NaN   
4256                                                NaN   
4257                                                NaN   
4258                                                NaN   

                                             Industries  \
0     Cloud Computing, Cloud Infrastructure, Cloud M...   
1     Artificial Intelligence, Cloud Infrastructure,...   
2     Cloud Infrastructure, Information Technology, ...   
3     Cloud Computing, Cloud Infrastructure, Cloud M...   
4     Cloud Infrastructure, Cloud Management, Inform...   
...                                                 ...   
4254  Cloud Storage, Information Technology, Profess...   
4255  Cloud Storage, Enterprise Software, Informatio...   
4256       Cloud Data Services, Cloud Storage, Software   
4257  Cloud Storage, Manufacturing, Medical Device, ...   
4258  Cloud Storage, Information Technology, IT Mana...   

                              Website  \
0     https://www.genesesolution.com/   
1                https://polyaxon.com   
2           https://www.mainstream.rs   
3          https://www.clustercs.com/   
4               https://www.replex.io   
...                               ...   
4254    https://www.backupaddict.com/   
4255    http://www.netconvergence.com   
4256        https://www.mylabbook.com   
4257             https://radmedix.com   
4258    https://knockoutpcrepair.com/   

                          Headquarters Location  \
0               London, England, United Kingdom   
1                       Berlin, Berlin, Germany   
2                   Belgrade, Vojvodina, Serbia   
3                 Bucharest, Bucuresti, Romania   
4                     Leipzig, Sachsen, Germany   
...                                         ...   
4254  Jersey Shore, Pennsylvania, United States   
4255     Santa Clara, California, United States   
4256       Texas, South Carolina, United States   
4257                Dayton, Ohio, United States   
4258       Brentwood, California, United States   

                                            Description CB Rank (Company)  \
0     As an official Cloud Consulting Provider of Am...           439,251   
1     An open source platform for reproducible machi...           208,230   
2     Mainstream provides advanced cloud, managed ho...           439,301   
3     ClusterCS is a Cloud-Based Linux Control Panel...           408,356   
4                   Replex provides software solutions.            26,882   
...                                               

In [98]:
crunch_data_r_selected = crunch_data_r.loc[crunch_data_r['PP text'] != "[]"]

In [99]:
crunch_data_r_selected

Organization Name  \
0                        Genese Solution   
1                               Polyaxon   
2                             Mainstream   
5                           Power DCloud   
7                              Red Kubes   
...                                  ...   
4238  Roanoke Valley Broadband Authority   
4239                  Data Security Corp   
4243                           archivedi   
4254                        BackupAddict   
4257                            Radmedix   

                                  Organization Name URL  \
0     https://www.crunchbase.com/organization/genese...   
1      https://www.crunchbase.com/organization/polyaxon   
2     https://www.crunchbase.com/organization/mainst...   
5     https://www.crunchbase.com/organization/power-...   
7     https://www.crunchbase.com/organization/red-kubes   
...                                                 ...   
4238  https://www.crunchbase.com/organization/roanok...   
4239  https://www.crunchbase.com/organization/data-s...   
4243  https://www.crunchbase.com/organization/archivedi   
4254  https://www.crunchbase.com/organization/backup...   
4257   https://www.crunchbase.com/organization/radmedix   

                                       Full Description  \
0     We are an official Cloud Consulting Provider o...   
1                                                   NaN   
2                                                   NaN   
5     Power Ecosystem is a web3 company, developer o...   
7     For all that Kubernetes can do, it still requi...   
...                                                 ...   
4238  RVBA offers local businesses secure, dependabl...   
4239                                                NaN   
4243                                                NaN   
4254                                                NaN   
4257                                                NaN   

                                             Industries  \
0     Cloud Computing, Cloud Infrastructure, Cloud M...   
1     Artificial Intelligence, Cloud Infrastructure,...   
2     Cloud Infrastructure, Information Technology, ...   
5     Blockchain, Cloud Infrastructure, Cloud Storag...   
7                        Cloud Infrastructure, Software   
...                                                 ...   
4238  Cloud Storage, Internet, Optical Communication...   
4239  Cloud Storage, Computer, Data Storage, Network...   
4243                            Cloud Storage, Software   
4254  Cloud Storage, Information Technology, Profess...   
4257  Cloud Storage, Manufacturing, Medical Device, ...   

                               Website  \
0      https://www.genesesolution.com/   
1                 https://polyaxon.com   
2            https://www.mainstream.rs   
5                  https://thepower.io   
7                https://redkubes.com/   
...                                ...   
4238               https://rvba.online   
4239  https://www.datasecuritycorp.com   
4243             https://archivedi.com   
4254     https://www.backupaddict.com/   
4257              https://radmedix.com   

                          Headquarters Location  \
0               London, England, United Kingdom   
1                       Berlin, Berlin, Germany   
2                   Belgrade, Vojvodina, Serbia   
5                    Tallinn, Harjumaa, Estonia   
7             Utrecht, Utrecht, The Netherlands   
...                                         ...   
4238           Roanoke, Virginia, United States   
4239          Tacoma, Washington, United States   
4243           Sarasota, Florida, United States   
4254  Jersey Shore, Pennsylvania, United States   
4257                Dayton, Ohio, United States   

                                            Description CB Rank (Company)  \
0     As an official Cloud Consulting Provider of Am...           439,251   
1     An open source platform for reproducible machi...           208,230   
2     Mainstream p

In [100]:
for index, row in crunch_data_r_selected.iterrows(): 
    x = row["PP text"]
    pp_text_split = x.split(', ')
    
    for j, category in enumerate(GDPR_classes):
             # Load from file to check if everything is ok
        filen = "linreg-oversampling-" + category + ".pkl"      
        with open(filen, 'rb') as file:
            vectorizer, lr = pickle.load(file)
            x = vectorizer.transform(pp_text_split)
        
            y_pred = lr.predict(x)
#             print(y_pred)
            n_pos_pred = list(y_pred).count(1)
#             print(n_pos_pred)
            
            
#             print("(" + str(n_pos_pred) + "/" + str(len(pp_text_split)) + ") >= " + str(thresholds[j]))
            if (n_pos_pred/len(pp_text_split)) >= thresholds[j]:
    #           MARK THE LABEL AS POSITIVE (1), DEFAULT STATE IS NEGATIVE (0)
#                 print("TRUE")
                crunch_data_r_selected.at[index, GDPR_classes[j]] = 1
            else:
                pass

In [101]:
crunch_data_r_selected

Organization Name  \
0                        Genese Solution   
1                               Polyaxon   
2                             Mainstream   
5                           Power DCloud   
7                              Red Kubes   
...                                  ...   
4238  Roanoke Valley Broadband Authority   
4239                  Data Security Corp   
4243                           archivedi   
4254                        BackupAddict   
4257                            Radmedix   

                                  Organization Name URL  \
0     https://www.crunchbase.com/organization/genese...   
1      https://www.crunchbase.com/organization/polyaxon   
2     https://www.crunchbase.com/organization/mainst...   
5     https://www.crunchbase.com/organization/power-...   
7     https://www.crunchbase.com/organization/red-kubes   
...                                                 ...   
4238  https://www.crunchbase.com/organization/roanok...   
4239  https://www.crunchbase.com/organization/data-s...   
4243  https://www.crunchbase.com/organization/archivedi   
4254  https://www.crunchbase.com/organization/backup...   
4257   https://www.crunchbase.com/organization/radmedix   

                                       Full Description  \
0     We are an official Cloud Consulting Provider o...   
1                                                   NaN   
2                                                   NaN   
5     Power Ecosystem is a web3 company, developer o...   
7     For all that Kubernetes can do, it still requi...   
...                                                 ...   
4238  RVBA offers local businesses secure, dependabl...   
4239                                                NaN   
4243                                                NaN   
4254                                                NaN   
4257                                                NaN   

                                             Industries  \
0     Cloud Computing, Cloud Infrastructure, Cloud M...   
1     Artificial Intelligence, Cloud Infrastructure,...   
2     Cloud Infrastructure, Information Technology, ...   
5     Blockchain, Cloud Infrastructure, Cloud Storag...   
7                        Cloud Infrastructure, Software   
...                                                 ...   
4238  Cloud Storage, Internet, Optical Communication...   
4239  Cloud Storage, Computer, Data Storage, Network...   
4243                            Cloud Storage, Software   
4254  Cloud Storage, Information Technology, Profess...   
4257  Cloud Storage, Manufacturing, Medical Device, ...   

                               Website  \
0      https://www.genesesolution.com/   
1                 https://polyaxon.com   
2            https://www.mainstream.rs   
5                  https://thepower.io   
7                https://redkubes.com/   
...                                ...   
4238               https://rvba.online   
4239  https://www.datasecuritycorp.com   
4243             https://archivedi.com   
4254     https://www.backupaddict.com/   
4257              https://radmedix.com   

                          Headquarters Location  \
0               London, England, United Kingdom   
1                       Berlin, Berlin, Germany   
2                   Belgrade, Vojvodina, Serbia   
5                    Tallinn, Harjumaa, Estonia   
7             Utrecht, Utrecht, The Netherlands   
...                                         ...   
4238           Roanoke, Virginia, United States   
4239          Tacoma, Washington, United States   
4243           Sarasota, Florida, United States   
4254  Jersey Shore, Pennsylvania, United States   
4257                Dayton, Ohio, United States   

                                            Description CB Rank (Company)  \
0     As an official Cloud Consulting Provider of Am...           439,251   
1     An open source platform for reproducible machi...           208,230   
2     Mainstream p

In [103]:
crunch_data_r_selected.to_csv("crunch_classified_p3.csv", sep='\t', header=True, index=False)